# Import Libraries

In [1]:
from gurobipy import *
import pandas as pd
%matplotlib inline
import matplotlib as mpl
import matplotlib.pyplot as plt
import pysd
import pandas as pd
import numpy as np
import geopandas as gp
import zipfile
import requests
import networkx as nx
import matplotlib.cm
import math
from math import radians, sin, cos, acos
from geopy.distance import geodesic
import requests
from bs4 import BeautifulSoup
from osgeo import ogr, osr
import matplotlib.cm as cmx
import matplotlib.colors as colors
from Circles.circles import circle
from shapely.geometry import Polygon, Point
from descartes import PolygonPatch
from shapely.ops import cascaded_union
import pickle
from mpl_toolkits.basemap import Basemap
from matplotlib.patches import Polygon
from matplotlib.collections import PatchCollection
from matplotlib.colors import Normalize
import datacompy
import warnings
warnings.filterwarnings("ignore")
import time

# Import Input Data (Model Parameters)

In [2]:
with open('Case3FinalDataParameters', 'rb') as fp:
    mhi = pickle.load(fp)
    chi = pickle.load(fp)
    Qi = pickle.load(fp)
    uio = pickle.load(fp)
    cio = pickle.load(fp)
    capi = pickle.load(fp)
    xiiinit = pickle.load(fp)
    B = pickle.load(fp)
    Pi = pickle.load(fp)
    Tcost = pickle.load(fp)

with open('Case3compDPs', 'rb') as fp:
    compDPslist = pickle.load(fp)
    compviablelist = pickle.load(fp)

with open('Case3Fijlist', 'rb') as fp:
    compFijlist = pickle.load(fp)

with open('Case3compcij', 'rb') as fp:
    compcijlist = pickle.load(fp)

with open('Case3compmij', 'rb') as fp:
    compmijlist = pickle.load(fp)



In [ ]:
DPslist = compDPslist[15][0:3]
cijlist = compcijlist[15][0:3]
Fijlist = compFijlist[15][0:3]
mijlist = compmijlist[15][0:3]
period = 0

## Extract Additional Parameters

In [3]:
def runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period):
    DPs = DPslist[solutionnumber]
    LDC = DPs.copy()
    Si = DPs.loc[:,'Supply']
    Dj = DPs.loc[:,'ActualDemand']
    Fij = Fijlist[solutionnumber]
    cij = cijlist[solutionnumber]
    mij = mijlist[solutionnumber]

    m = Model()

    # Add variables


    yhi = {} #flow of goods between supply nodes
    xii = {} #binary value equal to 1 if supply node i is to be opened for pre-positioning
    yij = {} #flow of goods from supply node i to demand node j
    xij = {} #Binary variable equal to 1 if demand node j is allocated to supply node i
    Fi = {} #maximum prepositioning time at supply node i

    #define yhi as integer
    for h in range(len(LDC)):
        for i in range(len(LDC)):
            yhi[(h,i)] = m.addVar(lb=0, vtype=GRB.INTEGER)

    #define xii as binary
    for i in range(len(LDC)):
        xii[i] = m.addVar(vtype=GRB.BINARY)

    #define yij as integer
    for i in range(len(LDC)):
          for j in range(len(DPs)):
                yij[(i,j)] = m.addVar(lb=0, vtype=GRB.INTEGER)

    #define xij as binary
    for i in range(len(LDC)):
          for j in range(len(DPs)):
                xij[(i,j)] = m.addVar(lb=0, vtype=GRB.BINARY)

    #define Fi as integer 
    for i in range(len(LDC)):
        Fi[i] = m.addVar(lb=0, vtype=GRB.INTEGER)

    m.update()

#     4 Ensures that the total number of supply nodes is maximum of p
#     m.addConstr(quicksum(xii[i] for i in range(len(LDC))) <= p)

    #5 ensures flow at node j from all supply nodes is not greater than amount demanded at j
    for j in range(len(DPs)):
        m.addConstr(quicksum(yij[(i,j)] for i in range(len(LDC))) <= Dj[j])

    #6 j is only assigned to i if goods can be delivered from i to j withink K hours
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(xij[(i,j)] <= xii[i])

    # ensures that if i is assigned to j, that the maximum pre-positioning time at i takes into account the amount of time before the typhoon reaches j
    for i in range(len(LDC)):
        for j in range(len(DPs)):
                m.addConstr(Fi[i] <= (1-xij[(i,j)])*Fij.iloc[i,i] + xij[(i,j)]*Fij.iloc[i,j])

    #7 Ensures that goods can only be prepositioned at i if the time needed for pre-position does not exceed the maximum pre-positioning time allowed at i
    for h in range(len(LDC)):
          for i in range(len(LDC)):
                m.addConstr(mhi.iloc[h,i]*xii[i] +
                            (1-xiiinit.iloc[i,0])*xii[i]*uio 
                            <= 
                            Fi[i]
                           )


    #8 Ensures that there is enough quantity of supply at node i to deliver to node j
    for i in range(len(LDC)):
        m.addConstr(quicksum(yij[(i,j)] for j in range(len(DPs))) 
                    <=
                    Qi.iloc[i,0] 
                    +
                    quicksum(yhi[(h,i)] for h in range(len(LDC))) 
                    -
                    quicksum(yhi[(i,h)] for h in range(len(LDC))) 
                    )

    #9 Ensures that the quantity of goods delivered from LDC i to DPs does not exceed the capacity of the LDC
    for i in range(len(LDC)):
        m.addConstr(xii[i]*capi.iloc[i,0]                
                            >= quicksum(yij[(i,j)] for j in range(len(DPs))))

    #10 Ensures that DP j is served only if j is allocated to i
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(yij[(i,j)] <= 1000000 * xij[(i,j)])

#     #11 Ensures the path is selected for delivery from LDC to DPs is available based on the forecast
#     for i in range(len(LDC)):
#         for j in range(len(DPs)):
#             m.addConstr(xij[(i,j)] <= Rij.iloc[i,j])

    #12 Ensures that supply node h has the quantity needed to deliver to supply node i
    for i in range(len(LDC)):
        m.addConstr(quicksum(yhi[(i,h)] for h in range(len(LDC))) <= Qi.iloc[i,0])
    
    #Ensures that no supply goods are pre-positioned to permanently placed goods
    for h in range(len(LDC)):
        for i in range(len(LDC)):
            m.addConstr(yhi[(i,h)] <= 1000000*(1-Pi.iloc[i,0])*(1-Pi.iloc[h,0]))

    #Ensures that no supply is prepositioned to a node that is potentially destroyed
    for i in range(len(LDC)):
        m.addConstr(quicksum(yhi[(h,i)] for h in range(len(LDC))) <= 1000000*(Si[i]))  
    
    #11 Ensures the path is selected for delivery from LDC to DPs is available based on the forecast
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(xij[(i,j)] <= (Si[i]))
    
#     #Ensures that the used budget is less than B
#     m.addConstr(quicksum(quicksum(
#                     chi.iloc[h,i]*yhi[(h,i)]
#                     for i in range(len(LDC))) for h in range(len(LDC))) 
#                     +
#                     quicksum(
#                     (1-xiiinit.iloc[i,0])*xii[i]*cio 
# #                         + 
# #                     xiiinit.iloc[i,0]*(1-xii[i])*cic
#                     for i in range(len(LDC)))
#                     +
#                     quicksum(quicksum(
#                     cij.iloc[i,j]*yij[(i,j)]
#                     for i in range(len(LDC))) for j in range(len(LDC))) + Tcost <= B)
        
    m.setParam("MIPGap", 1e-8)
    m.setParam("TimeLimit", 5.0)
    m.setParam("NodefileStart", 0.05)
    # #Set Objective Functions
    # Objective Function 1 Min Costs
    m.setObjectiveN(quicksum(quicksum(
                    chi.iloc[h,i]*yhi[(h,i)]
                    for i in range(len(LDC))) for h in range(len(LDC))) 
                    +
                    quicksum(
                    (1-xiiinit.iloc[i,0])*xii[i]*cio 
#                         + 
#                     xiiinit.iloc[i,0]*(1-xii[i])*cic
                    for i in range(len(LDC)))
                    +
                    quicksum(quicksum(
                    cij.iloc[i,j]*yij[(i,j)]
                    for i in range(len(LDC))) for j in range(len(LDC)))
                    , 
                    index=1, priority=1, weight=1 )

    #Objective Function 2 Min Supply Destroyed
    m.setObjectiveN(quicksum(quicksum(yij[(i,j)]*(mij.iloc[i,j])
                    for i in range(len(LDC))) for j in range(len(DPs))), 
                    index=2, priority=2, weight=1 )

    #Objective Function 3 Max Demand Supplied
    m.setObjectiveN(quicksum(quicksum(yij[(i,j)] 
                    for i in range(len(LDC))) for j in range(len(DPs))), 
                    index=3, priority=3, weight=-1)


    m.optimize()

    variablelist = m.getVars()
    variablelist = [i.x for i in variablelist]

    yhi = pd.DataFrame(np.array(variablelist[:len(DPs)**2]).reshape(len(DPs),len(DPs)))
    xii = pd.DataFrame(variablelist[len(DPs)**2:len(DPs)**2+len(DPs)])
    yij = pd.DataFrame(np.array(variablelist[len(DPs)**2+len(DPs):len(DPs)**2+len(DPs)+len(DPs)**2]).reshape(len(DPs),len(DPs)))
    xij = pd.DataFrame(np.array(variablelist[len(DPs)**2+len(DPs)+len(DPs)**2:len(DPs)**2+len(DPs)+len(DPs)**2+len(DPs)**2]).reshape(len(DPs),len(DPs)))
    Fi = pd.DataFrame(variablelist[len(DPs)**2+len(DPs)+len(DPs)**2+len(DPs)**2:])

    pd.set_option('display.max_columns', None)  
    yhi2 = yhi[(yhi.T != 0).any()]
    xii2 = xii[(xii.T != 0).any()]
    yij2 = yij[(yij.T != 0).any()]
    xij2 = xij[(xij.T != 0).any()]
    Fi2 = Fi[(Fi.T != 0).any()]
    
    costA = yij.copy()
    costB = xii.copy()
    dyij = yij.copy()
    dist = yij.copy()
    for i in range(len(dyij)):
        for j in range(len(dyij)):
            dyij.iloc[i,j] = yij.iloc[i,j]*(1-Si[i])
            costA.iloc[i,j] = chi.iloc[i,j]*yhi.iloc[i,j] + cij.iloc[i,j]*yij.iloc[i,j]
            dist.iloc[i,j] = yij.iloc[i,j]*cij.iloc[i,j]
    for i in range(len(costB)):
        costB.iloc[i,0] = (1-xiiinit.iloc[i,0])*xii.iloc[i,0]*cio
    
    Qinew = Qi.copy()
    DD = Qi.copy()
    for i in range(len(Qinew)):
        Qinew.iloc[i,0] = Qi.iloc[i,0] - yhi.sum(axis=1)[i] + yhi.sum(axis=0)[i]
        DD.iloc[i,0] = Qinew.iloc[i,0]*(1-Si[i])
    
    if yij.sum().sum() == 0:
        avedist = 0
    else:
        avedist = dist.sum().sum()/yij.sum().sum()
        
    
    listA = pd.DataFrame(np.zeros((1, 0)))
    listA['Period'] = period
    listA['Solution'] = solutionnumber
    listA['Demand'] = Dj.sum()
    listA['SuppliedDemand'] = yij.sum().sum()
    listA['DestroyedDemand'] = DD.sum().sum()
    listA['AverageDistance'] = avedist
    listA['Cost'] = Tcost + costA.sum().sum() + costB.sum()
    listA['Facilities'] = xii.sum()
    listA = pd.concat([listA, Qinew.T], axis=1)
    return listA, yhi, xii, yij, xij, Fi 

In [ ]:
yhilist = list()
xiilist = list()
yijlist = list()
xijlist = list()
Filist = list()
for solutionnumber in range(len(DPslist)):
    if solutionnumber == 0:
        ADF, yhi, xii, yij, xij, Fi = runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period)
    else:
        ADFnew, yhi, xii, yij, xij, Fi = runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period)
        ADF = ADF.append(ADFnew)
    yhilist.append(yhi)
    xiilist.append(xii)
    yijlist.append(yij)
    xijlist.append(xij)
    Filist.append(Fi)
ADF = ADF.reset_index(drop = True)

In [ ]:
ADF

In [4]:
def runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost):

    DPs = DPslist[scenarionumber]
    LDC = DPs.copy()
    Si = DPs.loc[:,'Supply']
    Dj = DPs.loc[:,'ActualDemand']
    Fij = Fijlist[scenarionumber]
    cij = cijlist[scenarionumber]
    mij = mijlist[scenarionumber]
    yhi = yhilist[solutionnumber]

    


    m = Model()


    # Add variables


    xii = {} #binary value equal to 1 if supply node i is to be opened for pre-positioning
    yij = {} #flow of goods from supply node i to demand node j
    xij = {} #Binary variable equal to 1 if demand node j is allocated to supply node i
    Fi = {} #maximum prepositioning time at supply node i

    #define xii as binary
    for i in range(len(LDC)):
        xii[i] = m.addVar(vtype=GRB.BINARY)

    #define yij as integer
    for i in range(len(LDC)):
          for j in range(len(DPs)):
                yij[(i,j)] = m.addVar(lb=0, vtype=GRB.INTEGER)

    #define xij as binary
    for i in range(len(LDC)):
          for j in range(len(DPs)):
                xij[(i,j)] = m.addVar(lb=0, vtype=GRB.BINARY)

    #define Fi as integer 
    for i in range(len(LDC)):
        Fi[i] = m.addVar(lb=0, vtype=GRB.INTEGER)

    m.update()


    #5 ensures flow at node j from all supply nodes is not greater than amount demanded at j
    for j in range(len(DPs)):
        m.addConstr(quicksum(yij[(i,j)] for i in range(len(LDC))) <= Dj[j])

    #6 j is only assigned to i if goods can be delivered from i to j withink K hours
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(xij[(i,j)] <= xii[i])

    # ensures that if i is assigned to j, that the maximum pre-positioning time at i takes into account the amount of time before the typhoon reaches j
    for i in range(len(LDC)):
        for j in range(len(DPs)):
                m.addConstr(Fi[i] <= (1-xij[(i,j)])*Fij.iloc[i,i] + xij[(i,j)]*Fij.iloc[i,j])

    #7 Ensures that goods can only be prepositioned at i if the time needed for pre-position does not exceed the maximum pre-positioning time allowed at i
    for h in range(len(LDC)):
          for i in range(len(LDC)):
                m.addConstr( 
                            mhi.iloc[h,i]*xii[i] +
                            (1-xiiinit.iloc[i,0])*xii[i]*uio 
                            <= 
                            Fi[i]
                           )


    #8 Ensures that there is enough quantity of supply at node i to deliver to node j
    for i in range(len(LDC)):
        m.addConstr(quicksum(yij[(i,j)] for j in range(len(DPs))) 
                    <=
                    Qi.iloc[i,0] - yhi.sum(axis=1)[i] + yhi.sum(axis=0)[i]
                    )

    #9 Ensures that the quantity of goods delivered from LDC i to DPs does not exceed the capacity of the LDC
    for i in range(len(LDC)):
        m.addConstr(xii[i]*capi.iloc[i,0]                
                            >= quicksum(yij[(i,j)] for j in range(len(DPs))))

    #10 Ensures that DP j is served only if j is allocated to i
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(yij[(i,j)] <= 1000000 * xij[(i,j)])

    #11 Ensures the path is selected for delivery from LDC to DPs is available based on the forecast
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            m.addConstr(xij[(i,j)] <= (Si[i]))
    

    m.setParam("MIPGap", 1e-8)
    m.setParam("TimeLimit", 5.0)
    m.setParam("NodefileStart", 0.05)
    # #Set Objective Functions
#     Objective Funciton 1 Min Costs
    m.setObjectiveN(quicksum(quicksum(
                    chi.iloc[h,i]*yhi.iloc[h,i]
                    for i in range(len(LDC))) for h in range(len(LDC))) 
                    +
                    quicksum(
                    (1-xiiinit.iloc[i,0])*xii[i]*cio 
                    for i in range(len(LDC)))
                    +
                    quicksum(quicksum(
                    cij.iloc[i,j]*yij[(i,j)]
                    for i in range(len(LDC))) for j in range(len(LDC)))
                    , 
                    index=1, priority=1, weight=1 )

    #Objective Function 2 Min Supply Destroyed
    m.setObjectiveN(quicksum(quicksum(yij[(i,j)]*(mij.iloc[i,j])
                    for i in range(len(LDC))) for j in range(len(DPs))), 
                    index=2, priority=2, weight=1 )

    #Objective Function 3 Max Demand Supplied
    m.setObjectiveN(quicksum(quicksum(yij[(i,j)] 
                    for i in range(len(LDC))) for j in range(len(DPs))), 
                    index=3, priority=3, weight=-1)



    m.optimize()

    variablelist = m.getVars()
    variablelist = [i.x for i in variablelist]

    xii = pd.DataFrame(variablelist[:len(DPs)])
    yij = pd.DataFrame(np.array(variablelist[len(DPs):len(DPs)+len(DPs)**2]).reshape(len(DPs),len(DPs)))
    xij = pd.DataFrame(np.array(variablelist[len(DPs)+len(DPs)**2:+len(DPs)+len(DPs)**2+len(DPs)**2]).reshape(len(DPs),len(DPs)))
    Fi = pd.DataFrame(variablelist[len(DPs)+len(DPs)**2+len(DPs)**2:])

    pd.set_option('display.max_columns', None)  
    yhi2 = yhi[(yhi.T != 0).any()]
    xii2 = xii[(xii.T != 0).any()]
    yij2 = yij[(yij.T != 0).any()]
    xij2 = xij[(xij.T != 0).any()]
    Fi2 = Fi[(Fi.T != 0).any()]

    costA = yij.copy()
    costB = xii.copy()
    dyhi = Si.copy()
    dist = yij.copy()
    for i in range(len(LDC)):
        for j in range(len(DPs)):
            #costA is the cost of transferring between supply nodes (h to i) and from supply nodes to demand nodes (i to j)
            costA.iloc[i,j] = chi.iloc[i,j]*yhi.iloc[i,j] + cij.iloc[i,j]*yij.iloc[i,j]
            dist.iloc[i,j] = yij.iloc[i,j]*cij.iloc[i,j]
    for i in range(len(LDC)):
        #costB is the cost of setup (and closure) and opened and closed nodeds
        costB.iloc[i,0] = (1-xiiinit.iloc[i,0])*xii.iloc[i,0]*cio 
#         + xiiinit.iloc[i,0]*(1-xii.iloc[i,0])*cic
        dyhi[i] = (1-Si[i])*yhi.sum(axis=0)[i]

    Qinew = Qi.copy()
    DD = Qi.copy()
    for i in range(len(Qinew)):
        Qinew.iloc[i,0] = Qi.iloc[i,0] - yhi.sum(axis=1)[i] + yhi.sum(axis=0)[i]
        DD.iloc[i,0] = Qinew.iloc[i,0]*(1-Si[i])
    
    
    if yij.sum().sum() == 0:
        avedist = 0
    else:
        avedist = dist.sum().sum()/yij.sum().sum()
       

    listA = pd.DataFrame(np.zeros((1, 0)))
    listA['Period'] = period
    listA['Scenario'] = scenarionumber
    listA['Solution'] = solutionnumber
    listA['Demand'] = Dj.sum()
    listA['SuppliedDemand'] = yij.sum().sum()
    listA['DestroyedDemand'] = DD.sum().sum()
    listA['AverageDistance'] = avedist
    listA['Cost'] = Tcost + costA.sum().sum() + costB.sum()
    listA['Facilities'] = xii.sum()
#     listA = pd.concat([listA, Qinew.T], axis=1)
    
    return listA

In [ ]:
for scenarionumber in range(len(DPslist)):
    for solutionnumber in range(len(DPslist)):
        if solutionnumber == 0 and scenarionumber == 0:
            BDF = runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost)
        else:
            BDF = BDF.append(runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost))

In [ ]:
BDF = BDF.reset_index(drop=True)
BDF

In [ ]:
maxSD = list()
mindist = list()
minC = list()

BDF2 = BDF.copy()
for i in range(len(BDF2)):
    if BDF2.loc[i,'Scenario'] == BDF2.loc[i,'Solution']:
        maxSD.append(BDF2.loc[i,'SuppliedDemand'])
        mindist.append(BDF2.loc[i,'AverageDistance'])
        minC.append(BDF2.loc[i,'Cost'])
    
for i in range(len(BDF2)):
    BDF2.loc[i,'SDabs'] = round(BDF2.loc[i,'SuppliedDemand']/BDF2.loc[i,'Demand']*100,2)
#     BDF2.loc[i,'DDabs'] = round(BDF2.loc[i,'DestroyedDemand']/BDF2.loc[i,'Demand']*100,2)
    BDF2.loc[i,'Dstabs'] = BDF2.loc[i,'AverageDistance']
    BDF2.loc[i,'Cabs'] = round(BDF2.loc[i,'Cost'],2)
    BDF2.loc[i, 'SDrel'] = round((maxSD[int(BDF2.loc[i,'Scenario'])] - BDF2.loc[i,'SuppliedDemand'])/ maxSD[int(BDF2.loc[i,'Scenario'])] *100,2)
#     BDF2.loc[i, 'DDrel'] = round((maxSD[int(BDF2.loc[i,'Scenario'])] - BDF2.loc[i,'DestroyedDemand'] )/maxSD[int(BDF2.loc[i,'Scenario'])]*100,2)
    BDF2.loc[i, 'Dstrel'] = round((BDF2.loc[i,'AverageDistance'] - mindist[int(BDF2.loc[i,'Scenario'])] ),2)
    BDF2.loc[i, 'Crel'] = BDF2.loc[i,'Cost'] - minC[int(BDF2.loc[i,'Scenario'])]
    
    
BDFmean = BDF2.groupby(['Solution']).mean()
BDFmax = BDF2.groupby(['Solution']).max()
# BDFmin = BDF3 = BDF2.groupby(['Solution']).min()
BDF2 = pd.concat([BDFmean.iloc[:,:11], BDFmax.iloc[:,11:]], axis=1)
abskey = None
relkey = None

abskeytent = np.argwhere(BDF2.SDabs.tolist() == np.amax(BDF2.SDabs.tolist())).flatten().tolist()
if len(abskeytent) > 1:
    BDF2new = BDF2.loc[abskeytent,:]
    newabskeytent = np.argwhere(BDF2new.Dstabs.tolist() == np.amin(BDF2new.Dstabs.tolist())).flatten().tolist()
    abskeytent = [abskeytent[i] for i in newabskeytent] 
    if len(abskeytent) > 1:
        BDF2new = BDF2.loc[abskeytent,:]
        newabskeytent = np.argwhere(BDF2new.Cabs.tolist() == np.amin(BDF2new.Cabs.tolist())).flatten().tolist()
        abskeytent = [abskeytent[i] for i in newabskeytent] 
abskey = abskeytent[0]


relkeytent = np.argwhere(BDF2.SDrel.tolist() == np.amin(BDF2.SDrel.tolist())).flatten().tolist()
if len(relkeytent) > 1:
    BDF2new = BDF2.loc[relkeytent,:]
    newrelkeytent = np.argwhere(BDF2new.Dstrel.tolist() == np.amin(BDF2new.Dstrel.tolist())).flatten().tolist()
    relkeytent = [relkeytent[i] for i in newrelkeytent ] 
    if len(relkeytent) > 1:
        print(relkeytent)
        BDF2new = BDF2.loc[relkeytent,:]
        newrelkeytent = np.argwhere(BDF2new.Crel.tolist() == np.amin(BDF2new.Crel.tolist())).flatten().tolist()
        relkeytent = [relkeytent[i] for i in newrelkeytent ]
relkey = relkeytent[0]

keycode = 'abs'
    

In [ ]:
abskey

In [ ]:
relkey

In [ ]:
if keycode == 'abs':
    key = abskey
elif keycode == 'rel':
    key = relkey

In [ ]:
minFij = Fijlist[0]*0+500
for i in range(len(Fijlist)):
    for j in range(len(Fijlist[0])):
        for k in range(len(Fijlist[0])):
            minFij.iloc[j,k] = min(Fijlist[i].iloc[j,k],minFij.iloc[j,k])

In [ ]:
#Strategy 1 - pre-position at the last minute

xijnew = xijlist[abskey]
xijnew = xijnew.replace({0:np.nan})
minprep = xijnew*minFij
minprep = minprep.min(axis=1)
minprep = minprep.to_frame()

mhinew = mhi.reset_index(drop=True)
mhinew.columns = range(mhinew.shape[1])
mhinew = mhinew*(yhilist[abskey]/yhilist[abskey])
mhinew = mhinew.max(axis=0).to_frame()
mhinew = mhinew.replace({np.nan:0})

preptime = (1-xiiinit)*xiilist[abskey]*uio + mhinew
extratime = minprep - preptime

for i in range(len(extratime)):
    if extratime.iloc[i,0] < 6:
        Pi.iloc[i,0] = 1

In [ ]:
yhicopy = yhilist[abskey].copy()
for i in range(len(yhilist[abskey])):
    for j in range(len(yhilist[abskey])):
        yhicopy.iloc[i,j] = yhicopy.iloc[i,j]*Pi.iloc[j,0]

for i in range(len(Qi)):
    Qi.iloc[i,0] = Qi.iloc[i,0] - yhicopy.sum(axis=1)[i] + yhicopy.sum(axis=0)[i]

In [ ]:
Tcost1 = yhicopy.copy()
Tcost2 = xiilist[key].copy()
for i in range(len(yhicopy)):
    for j in range(len(yhicopy)):
        Tcost1.iloc[i,j] = chi.iloc[i,j]*yhicopy.iloc[i,j] 
for i in range(len(xiilist[key])):
    Tcost2.iloc[i,0] = (1-xiiinit.iloc[i,0])*(Qi/Qi).iloc[i,0]*cio 

Tcost = Tcost + Tcost1.sum().sum() + Tcost2.sum().sum()
xiiinit = (Qi/Qi).replace({np.nan:0})
Pi.equals(xiilist[key])

In [ ]:
xiilist[key]

In [7]:
start_time = time.time()

ADFlist = list()
BDFlist = list()
BDF2list = list()
keylist = list()
Qilist = list()
Tcostlist = list()
xiiinitlist = list()
Pilist = list()
yijmasterlist = list()
yhimasterlist = list()
extratimelist = list()
preptimelist = list()

for period in range(len(compDPslist)):
    print('period %d' % period)
#     Qilist.append(Qi)
#     Pilist.append(Pi)
    print(Pi)
    print(Qi)
    if len(compDPslist[period])>1:
        DPslist = compDPslist[period]
        cijlist = compcijlist[period]
        Fijlist = compFijlist[period]
        mijlist = compmijlist[period]

        #RUN MODEL A
        yhilist = list()
        xiilist = list()
        yijlist = list()
        xijlist = list()
        Filist = list()
        for solutionnumber in range(len(DPslist)):
            if solutionnumber == 0:
                ADF, yhi, xii, yij, xij, Fi = runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period)
            else:
                ADFnew, yhi, xii, yij, xij, Fi = runmodelA(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, Pi, solutionnumber, Tcost, period)
                ADF = ADF.append(ADFnew)
            yhilist.append(yhi)
            xiilist.append(xii)
            yijlist.append(yij)
            xijlist.append(xij)
            Filist.append(Fi)
        ADF = ADF.reset_index(drop = True)
        
        ADFlist.append(ADF)
        
        
        #RUN MODEL B
        for scenarionumber in range(len(DPslist)):
            for solutionnumber in range(len(DPslist)):
                if solutionnumber == 0 and scenarionumber == 0:
                    BDF = runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost)
                else:
                    BDF = BDF.append(runmodelB(DPslist, mhi, chi, Qi, uio, cio, capi, xiiinit, cijlist, mijlist, Fijlist, B, solutionnumber, scenarionumber, period, yhilist, Tcost))

        BDF = BDF.reset_index(drop=True)
        BDFlist.append(BDF)
        
        
        #COMPUTE FOR BDF2 TO DETERMINE THE ROBUST SOLUTION
        maxSD = list()
        mindist = list()
        minC = list()

        BDF2 = BDF.copy()
        for i in range(len(BDF2)):
            if BDF2.loc[i,'Scenario'] == BDF2.loc[i,'Solution']:
                maxSD.append(BDF2.loc[i,'SuppliedDemand'])
                mindist.append(BDF2.loc[i,'AverageDistance'])
                minC.append(BDF2.loc[i,'Cost'])

        for i in range(len(BDF2)):
            BDF2.loc[i,'SDabs'] = round(BDF2.loc[i,'SuppliedDemand']/BDF2.loc[i,'Demand']*100,2)
        #     BDF2.loc[i,'DDabs'] = round(BDF2.loc[i,'DestroyedDemand']/BDF2.loc[i,'Demand']*100,2)
            BDF2.loc[i,'Dstabs'] = BDF2.loc[i,'AverageDistance']
            BDF2.loc[i,'Cabs'] = round(BDF2.loc[i,'Cost'],2)
            BDF2.loc[i, 'SDrel'] = round((maxSD[int(BDF2.loc[i,'Scenario'])] - BDF2.loc[i,'SuppliedDemand'])/ maxSD[int(BDF2.loc[i,'Scenario'])] *100,2)
        #     BDF2.loc[i, 'DDrel'] = round((maxSD[int(BDF2.loc[i,'Scenario'])] - BDF2.loc[i,'DestroyedDemand'] )/maxSD[int(BDF2.loc[i,'Scenario'])]*100,2)
            BDF2.loc[i, 'Dstrel'] = round((BDF2.loc[i,'AverageDistance'] - mindist[int(BDF2.loc[i,'Scenario'])] ),2)
            BDF2.loc[i, 'Crel'] = BDF2.loc[i,'Cost'] - minC[int(BDF2.loc[i,'Scenario'])]


        BDFmean = BDF2.groupby(['Solution']).mean()
        BDFmax = BDF2.groupby(['Solution']).max()
        # BDFmin = BDF3 = BDF2.groupby(['Solution']).min()
        BDF2 = pd.concat([BDFmean.iloc[:,:11], BDFmax.iloc[:,11:]], axis=1)
        abskey = None
        relkey = None
        
        BDF2list.append(BDF2)

        abskeytent = np.argwhere(BDF2.SDabs.tolist() == np.amax(BDF2.SDabs.tolist())).flatten().tolist()
        if len(abskeytent) > 1:
            BDF2new = BDF2.loc[abskeytent,:]
            newabskeytent = np.argwhere(BDF2new.Dstabs.tolist() == np.amin(BDF2new.Dstabs.tolist())).flatten().tolist()
            abskeytent = [abskeytent[i] for i in newabskeytent] 
            if len(abskeytent) > 1:
                BDF2new = BDF2.loc[abskeytent,:]
                newabskeytent = np.argwhere(BDF2new.Cabs.tolist() == np.amin(BDF2new.Cabs.tolist())).flatten().tolist()
                abskeytent = [abskeytent[i] for i in newabskeytent] 
        abskey = abskeytent[0]


        relkeytent = np.argwhere(BDF2.SDrel.tolist() == np.amin(BDF2.SDrel.tolist())).flatten().tolist()
        if len(relkeytent) > 1:
            BDF2new = BDF2.loc[relkeytent,:]
            newrelkeytent = np.argwhere(BDF2new.Dstrel.tolist() == np.amin(BDF2new.Dstrel.tolist())).flatten().tolist()
            relkeytent = [relkeytent[i] for i in newrelkeytent ] 
            if len(relkeytent) > 1:
                print(relkeytent)
                BDF2new = BDF2.loc[relkeytent,:]
                newrelkeytent = np.argwhere(BDF2new.Crel.tolist() == np.amin(BDF2new.Crel.tolist())).flatten().tolist()
                relkeytent = [relkeytent[i] for i in newrelkeytent ]
        relkey = relkeytent[0]
        
        #SPECIFY ROBUSTNESS CRITERIA
        keycode = 'rel'
        
        if keycode == 'abs':
            key = abskey
        elif keycode == 'rel':
            key = relkey
        
        keylist.append(key)
        
        #DETERMINE MINIMUM PREP TIME
        minFij = Fijlist[0]*0+500
        for i in range(len(Fijlist)):
            for j in range(len(Fijlist[0])):
                for k in range(len(Fijlist[0])):
                    minFij.iloc[j,k] = min(Fijlist[i].iloc[j,k],minFij.iloc[j,k])
        
        
        #Strategy 1 - pre-position at the last minute
        xijnew = xijlist[key]
        xijnew = xijnew.replace({0:np.nan})
        minprep = xijnew*minFij
        minprep = minprep.min(axis=1)
        minprep = minprep.to_frame()

        mhinew = mhi.reset_index(drop=True)
        mhinew.columns = range(mhinew.shape[1])
        mhinew = mhinew*(yhilist[key]/yhilist[key])
        mhinew = mhinew.max(axis=0).to_frame()
        mhinew = mhinew.replace({np.nan:0})

        preptime = (1-xiiinit)*xiilist[key]*uio + mhinew
        extratime = minprep - preptime

        for i in range(len(extratime)):
            if extratime.iloc[i,0] < 6:
                Pi.iloc[i,0] = 1

        yhicopy = yhilist[key].copy()
        for i in range(len(yhilist[key])):
            for j in range(len(yhilist[key])):
                yhicopy.iloc[i,j] = yhicopy.iloc[i,j]*Pi.iloc[j,0]

        for i in range(len(Qi)):
            Qi.iloc[i,0] = Qi.iloc[i,0] - yhicopy.sum(axis=1)[i] + yhicopy.sum(axis=0)[i]

        Tcost1 = yhicopy.copy()
        Tcost2 = xiilist[key].copy()
        for i in range(len(yhicopy)):
            for j in range(len(yhicopy)):
                Tcost1.iloc[i,j] = chi.iloc[i,j]*yhicopy.iloc[i,j] 
        for i in range(len(xiilist[key])):
            Tcost2.iloc[i,0] = (1-xiiinit.iloc[i,0])*(Qi/Qi).iloc[i,0]*cio 

        Tcost = Tcost + Tcost1.sum().sum() + Tcost2.sum().sum()
        xiiinit = (Qi/Qi).replace({np.nan:0})
        
        print(Pi.equals(xiilist[key]))
        Qi2 = Qi.copy()
        Pi2 = Pi.copy()
        Qilist.append(Qi2)
        Pilist.append(Pi2)
        
#         Qilist.append(Qi)
        Tcostlist.append(Tcost)
        xiiinitlist.append(xiiinit)
#         Pilist.append(Pi)
        yijmasterlist.append(yijlist[key])
        yhimasterlist.append(yhilist[key])
        extratimelist.append(extratime)
        preptimelist.append(preptime)
        
#         Pifake = Pi.copy()
#         Pifake.iloc[20,0] = 1
        
#         if Pifake.equals(xiilist[key]):
#             break
        
        
print("--- %s seconds ---" % (time.time() - start_time))      

    
    
    

period 0
      0
0   0.0
1   0.0
2   0.0
3   0.0
4   0.0
5   0.0
6   0.0
7   0.0
8   0.0
9   0.0
10  0.0
11  0.0
12  0.0
13  0.0
14  0.0
15  0.0
16  0.0
17  0.0
           0
0        0.0
1        0.0
2        0.0
3        0.0
4        0.0
5        0.0
6   300000.0
7        0.0
8        0.0
9        0.0
10       0.0
11       0.0
12       0.0
13       0.0
14       0.0
15       0.0
16       0.0
17       0.0
period 1
      0
0   0.0
1   0.0
2   0.0
3   0.0
4   0.0
5   0.0
6   0.0
7   0.0
8   0.0
9   0.0
10  0.0
11  0.0
12  0.0
13  0.0
14  0.0
15  0.0
16  0.0
17  0.0
           0
0        0.0
1        0.0
2        0.0
3        0.0
4        0.0
5        0.0
6   300000.0
7        0.0
8        0.0
9        0.0
10       0.0
11       0.0
12       0.0
13       0.0
14       0.0
15       0.0
16       0.0
17       0.0
period 2
      0
0   0.0
1   0.0
2   0.0
3   0.0
4   0.0
5   0.0
6   0.0
7   0.0
8   0.0
9   0.0
10  0.0
11  0.0
12  0.0
13  0.0
14  0.0
15  0.0
16  0.0
17  0.0
           0
0        0

Best objective 0.000000000000e+00, best bound 0.000000000000e+00, gap 0.0000%

---------------------------------------------------------------------------
Multi-objectives: solved in 0.20 seconds, solution count 4

Changed value of parameter MIPGap to 1e-08
   Prev: 0.0001  Min: 0.0  Max: 1e+100  Default: 0.0001
Changed value of parameter TimeLimit to 5.0
   Prev: 1e+100  Min: 0.0  Max: 1e+100  Default: 1e+100
Changed value of parameter NodefileStart to 0.05
   Prev: 1e+100  Min: 0.0  Max: 1e+100  Default: 1e+100
Optimize a model with 2034 rows, 1008 columns and 5210 nonzeros
Variable types: 0 continuous, 1008 integer (342 binary)
Coefficient statistics:
  Matrix range     [1e-01, 1e+06]
  Objective range  [1e-01, 3e+04]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 1e+06]

---------------------------------------------------------------------------
Multi-objectives: starting optimization with 4 objectives ... 
-------------------------------------------------------------

H    0     0                    1943579.8331 1914338.39  1.50%     -    0s
     0     0 1927079.61    0    7 1943579.83 1927079.61  0.85%     -    0s
     0     0 1927079.61    0    8 1943579.83 1927079.61  0.85%     -    0s
     0     0 1943579.82    0    3 1943579.83 1943579.82  0.00%     -    0s

Cutting planes:
  MIR: 1

Explored 1 nodes (81 simplex iterations) in 0.14 seconds
Thread count was 4 (of 4 available processors)

Solution count 2: 1.94358e+06 2.24058e+06 

Optimal solution found (tolerance 1.00e-08)
Best objective 1.943579833105e+06, best bound 1.943579818175e+06, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 4  ...
---------------------------------------------------------------------------


Loaded MIP start with objective 0


Explored 0 nodes (0 simplex iterations) in 0.17 seconds
Thread count was 1 (of 4 available processors)

Solution count 1: 0 

Optimal solution found (tolerance 1.00e-0


Root relaxation: objective 2.807863e+05, 15 iterations, 0.00 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0    280786.26583 280786.266  0.00%     -    0s

Explored 0 nodes (15 simplex iterations) in 0.09 seconds
Thread count was 4 (of 4 available processors)

Solution count 2: 280786 551651 

Optimal solution found (tolerance 1.00e-08)
Best objective 2.807862658333e+05, best bound 2.807862658333e+05, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 3 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 3.11162e+06

Presolve removed 386 rows and 282 columns
Presolve time: 0.00s
Presolved: 55 rows, 62 columns, 338 nonzeros
Variable types: 0 continuous, 62 integer (6 binary)

Root relaxation: cutoff, 27 iterat


    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0    -298092.0000 -298092.00  0.00%     -    0s

Explored 0 nodes (15 simplex iterations) in 0.05 seconds
Thread count was 4 (of 4 available processors)

Solution count 2: -298092 0 

Optimal solution found (tolerance 1.00e-08)
Best objective -2.980920000000e+05, best bound -2.980920000000e+05, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 2 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 705351

Presolve removed 406 rows and 288 columns
Presolve time: 0.00s
Presolved: 14 rows, 40 columns, 120 nonzeros
Variable types: 0 continuous, 40 integer (0 binary)

Root relaxation: objective 4.646140e+05, 21 iterations, 0.00 seconds

    Nodes    |    Current Node    |     O

...

---------------------------------------------------------------------------

Multi-objectives: optimize objective 3 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 141289

Presolve removed 64 rows and 78 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.11 seconds
Thread count was 1 (of 4 available processors)

Solution count 1: 141289 

Optimal solution found (tolerance 1.00e-08)
Best objective 1.412894436000e+05, best bound 1.412894436000e+05, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 4  ...
---------------------------------------------------------------------------


Loaded MIP start with objective 0


Explored 0 nodes (0 simplex iterations) in 0.12 seconds
Thread count was 1 (of 4 available processors)

Solution count 1: 0 

Optimal solution found (tolerance 1.00e-08)


Changed value of parameter TimeLimit to 5.0
   Prev: 1e+100  Min: 0.0  Max: 1e+100  Default: 1e+100
Changed value of parameter NodefileStart to 0.05
   Prev: 1e+100  Min: 0.0  Max: 1e+100  Default: 1e+100
Optimize a model with 1674 rows, 684 columns and 3667 nonzeros
Variable types: 0 continuous, 684 integer (342 binary)
Coefficient statistics:
  Matrix range     [1e-01, 1e+06]
  Objective range  [1e-01, 3e+04]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 3e+05]

---------------------------------------------------------------------------
Multi-objectives: starting optimization with 4 objectives ... 
---------------------------------------------------------------------------

Multi-objectives: applying initial presolve ...
---------------------------------------------------------------------------

Presolve removed 1625 rows and 617 columns
Presolve time: 0.00s
Presolved: 49 rows and 67 columns
---------------------------------------------------------------------------



Thread count was 1 (of 4 available processors)

Solution count 2: -60000 0 

Optimal solution found (tolerance 1.00e-08)
Best objective -6.000000000000e+04, best bound -6.000000000000e+04, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 2 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 114269

Presolve removed 62 rows and 67 columns
Presolve time: 0.00s
Presolved: 1 rows, 11 columns, 11 nonzeros
Variable types: 0 continuous, 11 integer (0 binary)

Root relaxation: objective 1.060260e+04, 1 iterations, 0.00 seconds

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0    10602.600000 10602.6000  0.00%     -    0s

Explored 0 nodes (1 simplex iterations) in 0.07 seconds
Thread count was 4 (of 4 available processors)

S


    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

*    0     0               0    10602.600000 10602.6000  0.00%     -    0s

Explored 0 nodes (1 simplex iterations) in 0.07 seconds
Thread count was 4 (of 4 available processors)

Solution count 2: 10602.6 114269 

Optimal solution found (tolerance 1.00e-08)
Best objective 1.060260000000e+04, best bound 1.060260000000e+04, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 3 () ...
---------------------------------------------------------------------------


Loaded MIP start with objective 141289

Presolve removed 64 rows and 78 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.09 seconds
Thread count was 1 (of 4 available processors)

Solution count 1: 141289 

Optimal solution found (tolerance 1.00

---------------------------------------------------------------------------


Loaded MIP start with objective 141289

Presolve removed 64 rows and 78 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.11 seconds
Thread count was 1 (of 4 available processors)

Solution count 1: 141289 

Optimal solution found (tolerance 1.00e-08)
Best objective 1.412894436000e+05, best bound 1.412894436000e+05, gap 0.0000%
---------------------------------------------------------------------------

Multi-objectives: optimize objective 4  ...
---------------------------------------------------------------------------


Loaded MIP start with objective 0


Explored 0 nodes (0 simplex iterations) in 0.12 seconds
Thread count was 1 (of 4 available processors)

Solution count 1: 0 

Optimal solution found (tolerance 1.00e-08)
Best objective 0.000000000000e+00, best bound 0.000000000000e+00, gap 0.0000%

--------------------------------------------

In [5]:
AA = compDPslist.copy()

for period in range(len(compDPslist)):
    for i in range(len(compDPslist[period])):
        if compDPslist[period][i].Supply.sum() == 18:
            AA[period][i] = 0
            compFijlist[period][i] = 0
            compcijlist[period][i] = 0
            compmijlist[period][i] = 0
            
AAlist = list()
BBlist = list()
CClist = list()
DDlist = list()
for period in range(len(AA)):
    A = list()
    B = list()
    C = list()
    D = list()
    for i in range(len(AA[period])):
        if isinstance(AA[period][i], pd.DataFrame):
            A.append(AA[period][i])
            B.append(compFijlist[period][i])
            C.append(compcijlist[period][i])
            D.append(compmijlist[period][i])
    AAlist.append(A)
    BBlist.append(B)
    CClist.append(C)
    DDlist.append(D)

    



In [6]:
compDPslist = AAlist.copy()[:19]
compFijlist = BBlist.copy()[:19]
compcijlist = CClist.copy()[:19]
compmijlist = DDlist.copy()[:19]

In [8]:
with open('ResultCase3REL', 'wb') as fp:
    pickle.dump(ADFlist, fp)
    pickle.dump(BDFlist, fp)
    pickle.dump(BDF2list, fp)
    pickle.dump(keylist, fp)
    pickle.dump(Qilist, fp)
    pickle.dump(Tcostlist, fp)
    pickle.dump(xiiinitlist, fp)
    pickle.dump(Pilist, fp)
    pickle.dump(yijmasterlist, fp)
    pickle.dump(yhimasterlist, fp)
    pickle.dump(extratimelist, fp)
    pickle.dump(preptimelist, fp)


In [ ]:
# with open('FINALILOILOABS', 'rb') as fp:
#     ADFlist = pickle.load(fp)
#     BDFlist = pickle.load(fp)
#     BDF2list = pickle.load(fp)
#     keylist = pickle.load(fp)
#     Qilist = pickle.load(fp)
#     Tcostlist = pickle.load(fp)
#     xiiinitlist = pickle.load(fp)
#     Pilist = pickle.load(fp)

In [8]:
Qilist

[           0
 0        0.0
 1        0.0
 2        0.0
 3        0.0
 4        0.0
 5        0.0
 6   300000.0
 7        0.0
 8        0.0
 9        0.0
 10       0.0
 11       0.0
 12       0.0
 13       0.0
 14       0.0
 15       0.0
 16       0.0
 17       0.0,            0
 0        0.0
 1        0.0
 2        0.0
 3        0.0
 4        0.0
 5        0.0
 6   300000.0
 7        0.0
 8        0.0
 9        0.0
 10       0.0
 11       0.0
 12       0.0
 13       0.0
 14       0.0
 15       0.0
 16       0.0
 17       0.0,            0
 0        0.0
 1        0.0
 2        0.0
 3        0.0
 4        0.0
 5        0.0
 6   300000.0
 7        0.0
 8        0.0
 9        0.0
 10       0.0
 11       0.0
 12       0.0
 13       0.0
 14       0.0
 15       0.0
 16       0.0
 17       0.0,            0
 0        0.0
 1        0.0
 2        0.0
 3        0.0
 4        0.0
 5        0.0
 6   300000.0
 7        0.0
 8        0.0
 9        0.0
 10       0.0
 11       0.0
 12       0.0
 13   

In [ ]:
keylist

In [ ]:
DPslist[0]

In [ ]:
capi